In [1]:
import pandas as pd
import json
import glob
from config import *

In [20]:
def query_db(query="*"):
    '''
    Pulls all of the current entries in the database and compiles them
    into a DataFrame. Creates compounding column names all starting with "data" to allow for
    nested keys to be reindexed later into their json files. Individual fragments are set as
    the index, i.e. a gene with two fragments would result in two different rows in the df.
    '''
    def crawl_dict(dictionary,name):
        '''
        Scans the dictionary to find the lowest level keys and their values, adds to a list of
        tuples and then returns the full list
        '''
        new_row = []
        for key in dictionary.keys():
            # The fragment sequences and locations columns are dictionaries
            # that have keys unique to the fragment name and so they need to
            # remain nested
            if key == "fragment_sequences" or key == "fragments":
                new_row = new_row + [(name+"."+key,dict(dictionary[key]))]
            elif type(dictionary[key]) == type(dict()):
                new_row += crawl_dict(dictionary[key],str(name+"."+key))
            elif type(dictionary[key]) == type(str()):
                new_row = new_row + [(name+"."+key,dictionary[key])]
#                 print(name+"."+key,"=",dictionary[key])
            elif type(dictionary[key]) == type(list()) and dictionary[key] != [""]:
                new_row += crawl_dict(dictionary[key][-1],str(name+"."+key))
            elif type(dictionary[key]) == type(bool()):
                if dictionary[key]:
                    new_row = new_row + [(name+"."+key,True)]
#                     print(name+"."+key,"=","True")
                else:
                    new_row = new_row + [(name+"."+key,False)]
#                     print(name+"."+key,"=","False")
            elif type(dictionary[key]) == type(int()):
                new_row = new_row + [(name+"."+key,dictionary[key])]
        return new_row

    # Iterates through all of the json files in the database and concatenates
    # all of the rows together to create the final dataframe
    full_db = pd.DataFrame()
    for file in glob.glob(BASE_PATH + "/data/*/BBF10K_{}.json".format(query)):
        with open(file,"r") as json_file:
            data = json.load(json_file)
        new_row = dict(crawl_dict(data,"data"))
        new_df = pd.DataFrame(new_row)
        full_db = pd.concat([full_db,new_df])
    return full_db
    
# full_db = query_db(query="000009")
# full_db = full_db.set_index("data.gene_id")
# full_db.to_csv("./test_dict.csv")
# full_db = full_db.sort_index()
# full_db["data.sequence.fragment_sequences"]
# full_db
        

In [21]:
full_db = query_db()

In [22]:
full_db
fillna_db = full_db.fillna("Empty")
full_db.to_csv('./full_db.csv')

In [23]:
print(full_db["data.info.order_number"].value_counts())



1    511
4    191
3     91
2     33
8     21
5      7
Name: data.info.order_number, dtype: int64


In [34]:
# numbers = range(0,len(full_db))
# full_db
full_db.groupby('data.status.build_complete')["data.status.build_complete"].count()
# full_db.groupby('data.info.order_number')["data.info.order_number"].count()
# full_db.groupby(['data.status.build_complete','data.gene_name'])["data.gene_name"].count()

data.status.build_complete
                            311
Bad_reads                     5
Good_sequence               377
Incomplete                   10
Original Vector Sequence     43
Original_vector_sequence     16
Partial                      13
Point Mutation                7
Point_mutation               44
Split Reads                   4
Unknown Sequence              1
Unknown_sequence             23
Name: data.status.build_complete, dtype: int64

In [14]:
# full_db = full_db[full_db['data.info.IP'] == '']
full_db['data.cloned.organism'].unique()
# full_db

array([''], dtype=object)

In [11]:
full_db["data.new"] = 1
full_db

data.author.affiliation         data.author.email  \
BBF10K_000001_1                  Stanford         endy@stanford.edu   
BBF10K_000002_1                  Stanford         endy@stanford.edu   
BBF10K_000003_1                  Stanford         endy@stanford.edu   
BBF10K_000004_1                  Stanford         endy@stanford.edu   
BBF10K_000005_1                  Stanford         endy@stanford.edu   
BBF10K_000006_1                  Stanford         endy@stanford.edu   
BBF10K_000006_2                  Stanford         endy@stanford.edu   
BBF10K_000007_1                  Stanford         endy@stanford.edu   
BBF10K_000007_2                  Stanford         endy@stanford.edu   
BBF10K_000008_1                  Stanford         endy@stanford.edu   
BBF10K_000009_1                  Stanford         endy@stanford.edu   
BBF10K_000009_2                  Stanford         endy@stanford.edu   
BBF10K_000010_1                  Stanford         endy@stanford.edu   
BBF10K_000011_1                  Stanford         endy@stanford.edu   
BBF10K_000012_1                  Stanford         endy@stanford.edu   
BBF10K_000013_1                  Stanford         endy@stanford.edu   
BBF10K_000014_1                  Stanford         endy@stanford.edu   
BBF10K_000015_1                  Stanford         endy@stanford.edu   
BBF10K_000016_1                  Stanford         endy@stanford.edu   
BBF10K_000017_1                  Stanford         endy@stanford.edu   
BBF10K_000017_2                  Stanford         endy@stanford.edu   
BBF10K_000018_1                  Stanford         endy@stanford.edu   
BBF10K_000018_2                  Stanford         endy@stanford.edu   
BBF10K_000018_3                  Stanford         endy@stanford.edu   
BBF10K_000018_4                  Stanford         endy@stanford.edu   
BBF10K_000019_1                  Stanford         endy@stanford.edu   
BBF10K_000019_2                  Stanford         endy@stanford.edu   
BBF10K_000020_1                  Stanford         endy@stanford.edu   
BBF10K_000021_1                  Stanford         endy@stanford.edu   
BBF10K_000022_1                  Stanford         endy@stanford.edu   
...                                   ...                       ...   
BBF10K_000631_1               ChiTown Bio          eyesmo@gmail.com   
BBF10K_000632_1               ChiTown Bio          eyesmo@gmail.com   
BBF10K_000633_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000634_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000635_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000636_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000637_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000638_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000639_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000654_1    Independent Researcher     coreyhowe99@gmail.com   
BBF10K_000655_1    Independent Researcher     coreyhowe99@gmail.com   
BBF10K_000656_1    Independent Researcher     coreyhowe99@gmail.com   
BBF10K_000657_1    Independent Researcher     coreyhowe99@gmail.com   
BBF10K_000658_1  Johns Hopkins University            joshua@jhu.edu   
BBF10K_000658_2  Johns Hopkins University            joshua@jhu.edu   
BBF10K_000659_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000660_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000661_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000662_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000663_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000663_2                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000664_1       Stanford University         endy@stanford.edu   
BBF10K_000664_2       Stanford University         endy@stanford.edu   
BBF10K_000665_1       Stanford University   alvinhuang@stanford.edu   
BBF10K_000665_2       Stanford University 

In [274]:
## Methods of pulling out specific data from the database
# full_db = full_db[full_db['data.gene_name'].str[:6] == 'MMSYN1']
# full_db = full_db[full_db['data.author.affiliation'] == 'Addgene']
# full_db = full_db[full_db['data.status.build_complete'] == 'Good_sequence']
# full_db.head()

In [5]:
def write_db(df):
    keys = df.columns.values
    for index, row in df.iterrows():
        with open(BASE_PATH + "/data/{}/{}.json".format(row["data.gene_id"],row["data.gene_id"]),"r") as json_file:
            data = json.load(json_file)
        for key,value in zip(keys,row):
            print(key)
            k = key.split(".")
            location = data
            for item in k[1:-1]:
                location = location[item]
                
                if key.startswith("data.cloned") and item == "cloned":
                    # Always choose the most recent clone
                    location = location[-1]
                    
            item = k[-1]
            
            if key == "data.sequence.fragment_sequences" or key == "data.location.fragments":
                location = location[index]
                print(location," = ",value)
                location[item] = value
#                 exec('{} = "{}"'.format(location,value))
#             elif key == 'data.cloned.organism':
            else:
                print("location[",item,"] = ",value)
                location[item] = value
#                 exec('{} = "{}"'.format(location,value))
        with open(BASE_PATH + "/data/{}/{}.json".format(row["data.gene_id"],row["data.gene_id"]),"w+") as json_file:
            json.dump(data,json_file,indent=2)

write_db(full_db)


data.author.affiliation
location[ affiliation ] =  Stanford
data.author.email
location[ email ] =  endy@stanford.edu
data.author.name
location[ name ] =  Stanford BIOE80 class 2017
data.author.orcid
location[ orcid ] =  
data.author.project
location[ project ] =  Build-A-Cell
data.cloned.organism
location[ organism ] =  
data.cloned.vector
location[ vector ] =  
data.dates.build_ready
location[ build_ready ] =  
data.dates.complete
location[ complete ] =  
data.dates.ordered
location[ ordered ] =  2017.07.24
data.dates.submitted
location[ submitted ] =  2017.07.24
data.description
location[ description ] =  None
data.gene_id
location[ gene_id ] =  BBF10K_000001
data.gene_name
location[ gene_name ] =  MMSYN1_0001
data.info.IP.results
location[ results ] =  Awaiting results
data.info.IP.submission_number
location[ submission_number ] =  002
data.info.collection
location[ collection ] =  JCVI syn3.0 genes codon optimized for E.coli
data.info.database_links
location[ database_links ] =  na

KeyError: 'BBF10K_000001_1'

In [19]:
def write_db(df):
    '''
    Takes in a data frame that has columns named "data.[something].[else]"
    and it uses those names to index into the json file corresponding to
    the rows gene_id. Pulls each json file, changes the attributes listed
    in the dataframe and rewrites the file.
    '''
    # Creates a list of the column names so that they can  be included in the
    # name of each column
    keys = df.columns.values
    for index, row in df.iterrows():
        with open(BASE_PATH + "/data/{}/{}.json".format(row["data.gene_id"],row["data.gene_id"]),"r") as json_file:
            data = json.load(json_file)
        for key,value in zip(keys,row):
            # Creates a python command to access the desired location in the
            # nested dictionary
            print(key)
            k = key.split(".")
            location = "data"
            for item in k[1:]:
                location = location + '["{}"]'.format(item)
                if item == 'cloned' or item == 'build_attempts':
                    location = location + "[-1]"
                
            # The fragment sequences and locations columns are dictionaries
            # that have keys unique to the fragment name and so those names
            # must be inserted
            
            elif key == "data.sequence.fragment_sequences" or key == "data.location.fragments":
                location = location + '["{}"]'.format(index)
#                 print(location," = ",value)
                exec('{} = "{}"'.format(location,value))
            else:
#                 print(location," = ",value)
                exec('{} = "{}"'.format(location,value))
        with open(BASE_PATH + "/data/{}/{}.json".format(row["data.gene_id"],row["data.gene_id"]),"w+") as json_file:
            json.dump(data,json_file,indent=2)
            
write_db(full_db)
full_db

data.author.affiliation
data["author"]["affiliation"]  =  Stanford
data.author.email
data["author"]["email"]  =  endy@stanford.edu
data.author.name
data["author"]["name"]  =  Stanford BIOE80 class 2017
data.author.orcid
data["author"]["orcid"]  =  
data.author.project
data["author"]["project"]  =  Build-A-Cell
data.cloned.organism
skip
data.cloned.vector
skip
data.dates.build_ready
data["dates"]["build_ready"]  =  
data.dates.complete
data["dates"]["complete"]  =  
data.dates.ordered
data["dates"]["ordered"]  =  2017.07.24
data.dates.submitted
data["dates"]["submitted"]  =  2017.07.24
data.description
data["description"]  =  None
data.gene_id
data["gene_id"]  =  BBF10K_000001
data.gene_name
data["gene_name"]  =  MMSYN1_0001
data.info.IP.results
data["info"]["IP"]["results"]  =  Awaiting results
data.info.IP.submission_number
data["info"]["IP"]["submission_number"]  =  002
data.info.collection
data["info"]["collection"]  =  JCVI syn3.0 genes codon optimized for E.coli
data.info.database

data["gene_id"]  =  BBF10K_000005
data.gene_name
data["gene_name"]  =  MMSYN1_0005
data.info.IP.results
data["info"]["IP"]["results"]  =  Awaiting results
data.info.IP.submission_number
data["info"]["IP"]["submission_number"]  =  002
data.info.collection
data["info"]["collection"]  =  JCVI syn3.0 genes codon optimized for E.coli
data.info.database_links
data["info"]["database_links"]  =  nan
data.info.order_week
data["info"]["order_week"]  =  2017.30
data.info.other_tags
data["info"]["other_tags"]  =  null
data.info.safety
data["info"]["safety"]  =  null
data.info.type.build_type
data["info"]["type"]["build_type"]  =  10K_MoClo-EntryCDS-BbsI
data.info.type.cloning_method
data["info"]["type"]["cloning_method"]  =  10K_MoClo
data.info.type.part_type
data["info"]["type"]["part_type"]  =  CDS
data.location.fragments
data["location"]["fragments"]["BBF10K_000005_1"]  =  pSHPs0807B412040MU_D2
data.project_description
data["project_description"]  =  nan
data.sequence.fragment_sequences
data["s

data["status"]["build_ready"]  =  nan
data.status.building
data["status"]["building"]  =  nan
data.new
data["new"]  =  1
data.author.affiliation
data["author"]["affiliation"]  =  Stanford
data.author.email
data["author"]["email"]  =  endy@stanford.edu
data.author.name
data["author"]["name"]  =  Stanford BIOE80 class 2017
data.author.orcid
data["author"]["orcid"]  =  
data.author.project
data["author"]["project"]  =  Build-A-Cell
data.cloned.organism
skip
data.cloned.vector
skip
data.dates.build_ready
data["dates"]["build_ready"]  =  
data.dates.complete
data["dates"]["complete"]  =  
data.dates.ordered
data["dates"]["ordered"]  =  2017.07.24
data.dates.submitted
data["dates"]["submitted"]  =  2017.07.24
data.description
data["description"]  =  None
data.gene_id
data["gene_id"]  =  BBF10K_000009
data.gene_name
data["gene_name"]  =  MMSYN1_0009
data.info.IP.results
data["info"]["IP"]["results"]  =  Awaiting results
data.info.IP.submission_number
data["info"]["IP"]["submission_number"]  =

skip
data.cloned.vector
skip
data.dates.build_ready
data["dates"]["build_ready"]  =  
data.dates.complete
data["dates"]["complete"]  =  
data.dates.ordered
data["dates"]["ordered"]  =  2017.07.24
data.dates.submitted
data["dates"]["submitted"]  =  2017.07.24
data.description
data["description"]  =  None
data.gene_id
data["gene_id"]  =  BBF10K_000016
data.gene_name
data["gene_name"]  =  MMSYN1_0030
data.info.IP.results
data["info"]["IP"]["results"]  =  Awaiting results
data.info.IP.submission_number
data["info"]["IP"]["submission_number"]  =  002
data.info.collection
data["info"]["collection"]  =  JCVI syn3.0 genes codon optimized for E.coli
data.info.database_links
data["info"]["database_links"]  =  nan
data.info.order_week
data["info"]["order_week"]  =  2017.30
data.info.other_tags
data["info"]["other_tags"]  =  null
data.info.safety
data["info"]["safety"]  =  null
data.info.type.build_type
data["info"]["type"]["build_type"]  =  10K_MoClo-EntryCDS-BbsI
data.info.type.cloning_method
da

data["sequence"]["fragment_sequences"]["BBF10K_000019_2"]  =  GAAGACATTCGCCCAGGTCGTTTTGACCGCGTGATCCAGGTTTCTTTACCTGACATCAAGGAGCGCGAACAAATCTTAAAGCTTCACGCGCGCAATAAGAAGATTGATCCGTCTATTGATTGGCACCGGATCGCGGAGCGCACTCCCGGCTTCAGTGGCGCACAGCTTGAAAACGTGTTAAATGAGGCTGCAATCCTGATGGTTCGCGAAGGTAAGACTGTAATTGGTATTAACGAAATTGATGAAGCGATCGATCGTGTAGTGGGAGGTCCTGCTAAGAAGTCACGTGCAATGACCATGCATGACAAGGAAATCGTTTCCTATCATGAGTCCGGGCACGCTCTGATCGGACTGAAACTTGAATCGGCATCTAAAGTTCAGAAGGTTACGATCATTCCGCGCGGCAACGCAGGAGGATACACAATCATGACTCCTAAGGATGAGACTCTTTTTTCAAGCAAAACTGACCTGTACGCCATGATTGCTGGATACCTGGGAGGACGCGCTGCGGAGGAAATTAAGTTCGGGAAAGATAACGTCACCACGGGTGCACATGATGATTTCGACAAAGCTACAGCGATTGCACGCCGTATGGTTATGCAATTTGGGATGTCCGAACTTGGAATCACAAAGTTTTTAACAATGGCTGACGAAGCATACGGCAAAACGGAGGGCAGCTACAGCGAAAAGACAGCGGCAAAGATCGATGCCGAGGTCGAGCGCATCCTGGAAGAGTCTTATAAACTGGCAATTAAGGTCATTAGTGAGAATATGGAAACATTAGAGTTGTTGGCTGAATCTCTTCGCGTGTTAGAGACTATCACAGCAGAGCAGATTGATTACATCAATAAAAACAAAAAGCTGCCCGAGGCCGTGATTTACGAAAAAGAAAAGTATAAACAGGAGCAGGAAAAAATCAACAGTGGAAAAATTATCGA

...

data["status"]["building"]  =  nan
data.new
data["new"]  =  1
data.author.affiliation
data["author"]["affiliation"]  =  ChiTown Bio
data.author.email
data["author"]["email"]  =  eyesmo@gmail.com
data.author.name
data["author"]["name"]  =  Isaac Larkin
data.author.orcid
data["author"]["orcid"]  =  
data.author.project
data["author"]["project"]  =  null
data.cloned.organism
skip
data.cloned.vector
skip
data.dates.build_ready
data["dates"]["build_ready"]  =  
data.dates.complete
data["dates"]["complete"]  =  
data.dates.ordered
data["dates"]["ordered"]  =  2017.10.09
data.dates.submitted
data["dates"]["submitted"]  =  2017.10.09
data.description
data["description"]  =  None
data.gene_id
data["gene_id"]  =  BBF10K_000632
data.gene_name
data["gene_name"]  =  Tardigrade CAHS 89226
data.info.IP.results
data["info"]["IP"]["results"]  =  Awaiting results
data.info.IP.submission_number
data["info"]["IP"]["submission_number"]  =  003
data.info.collection
data["info"]["collection"]  =  null
data.i

data.sequence.optimized_sequence
data["sequence"]["optimized_sequence"]  =  ATGAGTTCAGGCGCATTGCTTTTCCACGGCAAGATTCCCTATGTAGTCGAGATGGAAGGCAATGTTGACGGCCACACCTTCTCCATCCGCGGTAAGGGCTACGGCGACGCGAGTGTTGGCAAAGTCGATGCACAATTTATCTGCACCACCGGGGATGTCCCAGTGCCATGGTCAACTTTAGTGACAACCTTGACTTATGGTGCCCAGTGCTTTGCGAAGTATGGGCCTGGCCTTAAAGATTTTTATAAGTCATGCATGCCGGAAGGTTACGTCCAAGAACGTACCATTACGTTTGAGGGTGATGGTGTTTTCAAGACTCGTGCCGAGGTAACGTTTGAGAACGGCTCTGTTTACAACCGTGTGAAACTTAATGGGCAAGGGTTCAAGAAAGACGGGCATGTGCTTGGGAAGAATTTGGAGTTTAATTTTACTCCGCACTGTCTTTACATTTGGGGGGACCAGGCCAACCACGGACTGAAATCTGCATTCAAGATTATGCACGAGATTACCGGGTCAAAAGAGGATTTTATCGTTGCAGATCACACCCAGATGAACACCCCCATCGGGGGAGGCCCTGTCCATGTACCAGAATACCACCATTTGACCGTTTGGACCAGTTTCGGCAAGGACCCTGATGATGACGAAACGGACCACCTGAACATCGTGGAAGTCATTAAAGCTGTAGACCTTGAAACATACCGCTGA
data.sequence.original_sequence
data["sequence"]["original_sequence"]  =  ATGAGTTCAGGCGCATTGCTTTTCCACGGCAAGATTCCCTATGTAGTCGAGATGGAAGGCAATGTTGACGGCCACACCTTCTCCATCCGCGGTAAGGGCTACGGCGACGCGAGTGTTGGCAAAGTCGATGCACAATTTATCTGC

data["status"]["build_attempts"][-1]["build_date"]  =  
data.status.build_attempts.build_number
data["status"]["build_attempts"][-1]["build_number"]  =  
data.status.build_attempts.build_outcome
data["status"]["build_attempts"][-1]["build_outcome"]  =  
data.status.build_attempts.build_well
data["status"]["build_attempts"][-1]["build_well"]  =  
data.status.build_complete
data["status"]["build_complete"]  =  
data.status.build_ready
data["status"]["build_ready"]  =  
data.status.building
data["status"]["building"]  =  
data.new
data["new"]  =  1
data.author.affiliation
data["author"]["affiliation"]  =  NASA Ames
data.author.email
data["author"]["email"]  =  nils.j.averesch@nasa.gov
data.author.name
data["author"]["name"]  =  Nils Averesch
data.author.orcid
data["author"]["orcid"]  =   https://orcid.org/0000-0002-6389-2646
data.author.project
data["author"]["project"]  =  Bacillus subtilis aminobenzoates biosynthesis
data.cloned.organism
skip
data.cloned.vector
skip
data.dates.build_rea

data["status"]["building"]  =  
data.new
data["new"]  =  1
data.author.affiliation
data["author"]["affiliation"]  =  Stanford University
data.author.email
data["author"]["email"]  =  alvinhuang@stanford.edu
data.author.name
data["author"]["name"]  =  Alvin Huang
data.author.orcid
data["author"]["orcid"]  =  
data.author.project
data["author"]["project"]  =  Alvin Huang interesting genes
data.cloned.organism
skip
data.cloned.vector
skip
data.dates.build_ready
data["dates"]["build_ready"]  =  
data.dates.complete
data["dates"]["complete"]  =  
data.dates.ordered
data["dates"]["ordered"]  =  
data.dates.submitted
data["dates"]["submitted"]  =  
data.description
data["description"]  =  nan
data.gene_id
data["gene_id"]  =  BBF10K_000666
data.gene_name
data["gene_name"]  =  Homo sapiens SORL1
data.info.IP.results
data["info"]["IP"]["results"]  =  
data.info.IP.submission_number
data["info"]["IP"]["submission_number"]  =  
data.info.collection
data["info"]["collection"]  =  
data.info.databas

data.author.affiliation         data.author.email  \
BBF10K_000001_1                  Stanford         endy@stanford.edu   
BBF10K_000002_1                  Stanford         endy@stanford.edu   
BBF10K_000003_1                  Stanford         endy@stanford.edu   
BBF10K_000004_1                  Stanford         endy@stanford.edu   
BBF10K_000005_1                  Stanford         endy@stanford.edu   
BBF10K_000006_1                  Stanford         endy@stanford.edu   
BBF10K_000006_2                  Stanford         endy@stanford.edu   
BBF10K_000007_1                  Stanford         endy@stanford.edu   
BBF10K_000007_2                  Stanford         endy@stanford.edu   
BBF10K_000008_1                  Stanford         endy@stanford.edu   
BBF10K_000009_1                  Stanford         endy@stanford.edu   
BBF10K_000009_2                  Stanford         endy@stanford.edu   
BBF10K_000010_1                  Stanford         endy@stanford.edu   
BBF10K_000011_1                  Stanford         endy@stanford.edu   
BBF10K_000012_1                  Stanford         endy@stanford.edu   
BBF10K_000013_1                  Stanford         endy@stanford.edu   
BBF10K_000014_1                  Stanford         endy@stanford.edu   
BBF10K_000015_1                  Stanford         endy@stanford.edu   
BBF10K_000016_1                  Stanford         endy@stanford.edu   
BBF10K_000017_1                  Stanford         endy@stanford.edu   
BBF10K_000017_2                  Stanford         endy@stanford.edu   
BBF10K_000018_1                  Stanford         endy@stanford.edu   
BBF10K_000018_2                  Stanford         endy@stanford.edu   
BBF10K_000018_3                  Stanford         endy@stanford.edu   
BBF10K_000018_4                  Stanford         endy@stanford.edu   
BBF10K_000019_1                  Stanford         endy@stanford.edu   
BBF10K_000019_2                  Stanford         endy@stanford.edu   
BBF10K_000020_1                  Stanford         endy@stanford.edu   
BBF10K_000021_1                  Stanford         endy@stanford.edu   
BBF10K_000022_1                  Stanford         endy@stanford.edu   
...                                   ...                       ...   
BBF10K_000631_1               ChiTown Bio          eyesmo@gmail.com   
BBF10K_000632_1               ChiTown Bio          eyesmo@gmail.com   
BBF10K_000633_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000634_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000635_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000636_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000637_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000638_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000639_1      BioBricks Foundation        koeng101@gmail.com   
BBF10K_000654_1    Independent Researcher     coreyhowe99@gmail.com   
BBF10K_000655_1    Independent Researcher     coreyhowe99@gmail.com   
BBF10K_000656_1    Independent Researcher     coreyhowe99@gmail.com   
BBF10K_000657_1    Independent Researcher     coreyhowe99@gmail.com   
BBF10K_000658_1  Johns Hopkins University            joshua@jhu.edu   
BBF10K_000658_2  Johns Hopkins University            joshua@jhu.edu   
BBF10K_000659_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000660_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000661_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000662_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000663_1                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000663_2                 NASA Ames  nils.j.averesch@nasa.gov   
BBF10K_000664_1       Stanford University         endy@stanford.edu   
BBF10K_000664_2       Stanford University         endy@stanford.edu   
BBF10K_000665_1       Stanford University   alvinhuang@stanford.edu   
BBF10K_000665_2       Stanford University 

In [ ]:

def refine_db(db,dictionary):
    result = pd.DataFrame()
    def make_array(db,key,value):
        print("key",key,"value",value)
        array = pd.Series([item for item in db[key] if value in item]).unique()
        print(array,"\n")
        return array
    
    for key in dictionary:
        array = make_array(db,key,dictionary[key])
        for item in array:
            print("item",item,"key",key)
            db = db[db[key] == item]
            result = pd.concat([result,db])
    return result
# good_seqs = full_db[full_db['build_complete'] == "Good_sequence"]
# good_seqs
# names = [name for name in good_seqs["gene_name"] if "MMSYN1" in name]
# print(names)
# result = pd.DataFrame()

# results = good_seqs[good_seqs['gene_name'] == "MMSYN1_0002"]

# for name in names:
#     jcvi = good_seqs[good_seqs['gene_name'] == name]
#     result = pd.concat([result,jcvi])
# jcvi = good_seqs[good_seqs['gene_name'] == name]

    
# dictionary = {'gene_name':'MMSYN1_0007'} 
dictionary = {'build_complete':'Good'}
result = refine_db(full_db,dictionary)

    
result.to_csv("./test_dict.csv")

result